# Assignment 6

In this assignment, you'll analyze a collection of data sets from the [San Francisco Open Data Portal](http://data.sfgov.org/) and [Zillow](https://www.zillow.com/). The data sets have been stored in the SQLite database `sf_data.sqlite`, which you can [download here](http://anson.ucdavis.edu/~nulle/sf_data.sqlite). The database contains the following tables:

Table                   | Description
----------------------- | -----------
`crime`                 | Crime reports dating back to 2010.
`mobile_food_locations` | List of all locations where mobile food vendors sell.
`mobile_food_permits`   | List of all mobile food vendor permits. More details [here](https://data.sfgov.org/api/views/rqzj-sfat/files/8g2f5RV4PEk0_b24iJEtgEet9gnh_eA27GlqoOjjK4k?download=true&filename=DPW_DataDictionary_Mobile-Food-Facility-Permit.pdf).
`mobile_food_schedule`  | Schedules for mobile food vendors.
`noise`                 | Noise complaints dating back to August 2015.
`parking`               | List of all parking lots.
`parks`                 | List of all parks.
`schools`               | List of all schools.
`zillow`                | Zillow rent and housing statistics dating back to 1996. More details [here](https://www.zillow.com/research/data/).

The `mobile_food_` tables are explicitly connected through the `locationid` and `permit` columns. The other tables are not connected, but you may be able to connect them using dates, latitude/longitude, or postal codes.

Shapefiles for US postal codes are available [here](https://www.census.gov/geo/maps-data/data/cbf/cbf_zcta.html). These may be useful for converting latitude/longitude to postal codes.

Shapefiles for San Francisco Neighborhoods are available [here](https://data.sfgov.org/Geographic-Locations-and-Boundaries/SF-Find-Neighborhoods/pty2-tcw4).

In [1]:
import sqlite3 as sql
import pandas as pd
import plotly.plotly as py
from plotly.graph_objs import *
from plotly import __version__, tools
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
import plotly.graph_objs as go
init_notebook_mode()
mapbox_access_token = 'pk.eyJ1IjoiYWxpY2U0OTI2IiwiYSI6ImNqMDRjeGExMTBmdTgyeGxzNG15M3BpNnkifQ.-HeMotv3RitjmVgzTNl-yg'

In [2]:
db = sql.connect("sf_data.sqlite")

In [3]:
db.execute("SELECT * FROM sqlite_master")

In [4]:
pd.read_sql("SELECT * FROM sqlite_master", db)

type                   name               tbl_name  rootpage  \
0  table                  crime                  crime         2   
1  table                  noise                  noise     35775   
2  table                parking                parking     35921   
3  table                schools                schools     35944   
4  table                  parks                  parks     35961   
5  table                 zillow                 zillow     35967   
6  table    mobile_food_permits    mobile_food_permits     36050   
7  table  mobile_food_locations  mobile_food_locations     36060   
8  table   mobile_food_schedule   mobile_food_schedule     36079   

                                                 sql  
0  CREATE TABLE "crime" (\n"IncidntNum" INTEGER,\...  
1  CREATE TABLE "noise" (\n"CaseID" INTEGER,\n  "...  
2  CREATE TABLE "parking" (\n"Owner" TEXT,\n  "Ad...  
3  CREATE TABLE "schools" (\n"Name" TEXT,\n  "Ent...  
4  CREATE TABLE "parks" (\n"Name" TEXT,\n  "Type"...  
5  CREATE TABLE "zillow" (\n"RegionName" INTEGER,...  
6  CREATE TABLE "mobile_food_permits" (\n"permit"...  
7  CREATE TABLE "mobile_food_locations" (\n"locat...  
8  CREATE TABLE "mobile_food_schedule" (\n"locati...

__Exercise 1.1.__ Which mobile food vendor(s) sells at the most locations?

In [5]:
pd.read_sql("SELECT p.permit, p.Applicant, "
            "COUNT( DISTINCT s.locationid )as LocationCount "
            "FROM mobile_food_permits AS p LEFT JOIN mobile_food_schedule as s "
            "ON s.permit = p.permit "
            "GROUP BY Applicant "
            "ORDER BY LocationCount DESC "
            "LIMIT 5"
            , db)

permit              Applicant  LocationCount
0  17MFF-0110           May Catering             58
1  17MFF-0111  Anas Goodies Catering             37
2  17MFF-0123       Natan's Catering             37
3  17MFF-0090         Liang Bai Ping             33
4  16MFF-0051        Park's Catering             23

<font color = "blue">
May Catering sells at the most locations. It sells at 58 different location.

__Exercise 1.2.__ Ask and use the database to analyze 5 questions about San Francisco. For each question, write at least 150 words and support your answer with plots. Make a map for at least 2 of the 5 questions.

You should try to come up with some questions on your own, but these are examples of reasonable questions:

* Which parts of the city are the most and least expensive?
* Which parts of the city are the most dangerous (and at what times)?
* Are noise complaints and mobile food vendors related?
* What are the best times and places to find food trucks?
* Is there a relationship between housing prices and any of the other tables?

Please make sure to clearly state each of your questions in your submission.

__1. Does the number of school affect the housing price?__

<font color = "blue">
In this question, we are interested in whether how many the school is under each zipcode affect the housing price for each zipcode. In order to get this, we have to transfer the address of school data into zipcode and compute the total counts of school in each zipcode. After that, I find out the zipcode with top 3 school count and that with least 7 counts. The reason why I select 7 instead of 3 is that I found out there are lots of missing value of the housing price of zipcode which has less school, and for some zipcode, there is even not any housing price. 

I first plot the housing price from 2010 to 2017. After doing this, I found out that there are only 4 housing price in 94158. I can not use this four points to represent the median housing price in 94158 from 2010 to 2017, therefore I delete 94158 and plot the second plot(which you can see in below). 

In [6]:
school = pd.read_sql("SELECT Name , SUBSTR(Address,-5) AS zipcode FROM schools",db)
school.head(2)

Name zipcode
0     Alamo Elementary School   94121
1  Alvarado Elementary School   94114

In [7]:
school_per_zipcode = pd.DataFrame([{"RegionName": int(x), "schoolcount":list(school.zipcode).count(x)} for x in set(school.zipcode)]).sort_values("schoolcount", ascending=False)
top3 = school_per_zipcode.head(3).copy()
last7 = school_per_zipcode.tail(7).copy()
top3["group"] = "more"
last7["group"] = "few"
school_indicator = pd.concat([top3,last7])
school_indicator 

RegionName  schoolcount group
8        94110           41  more
13       94115           37  more
6        94118           29  more
20       94109           10   few
19       94129            7   few
25       94105            6   few
9        94111            2   few
22       94143            2   few
0        94130            2   few
5        94158            1   few

In [8]:
houseprice = pd.read_sql("SELECT RegionName, Date, MedianSoldPricePerSqft_AllHomes as Median_price FROM zillow "
                         "WHERE RegionName IN "
                         + str(tuple([str(item) for item in set(school_indicator.RegionName)])) +
                         " AND Date between '2010-01-01 00:00:00' and '2017-01-01 00:00:00'"
                         "ORDER BY RegionName",db)
houseprice = pd.merge(houseprice,school_indicator,on="RegionName")

In [9]:
set(houseprice.RegionName)

{94105, 94109, 94110, 94111, 94115, 94118, 94158}

In [10]:
from datetime import datetime
houseprice.Date = [datetime.strptime(x, '%Y-%m-%d %H:%M:%S').strftime('%Y-%m-%d') for x in houseprice.Date.tolist()]
houseprice.head()
houseprice["Date"] = houseprice["Date"].astype("datetime64[ns]")
houseprice.dtypes
houseprice = houseprice.set_index("Date")

RegionName  Median_price  schoolcount group
Date                                                   
2010-11-01       94105           NaN            6   few
2010-12-01       94105    633.161100            6   few
2011-01-01       94105           NaN            6   few
2011-02-01       94105           NaN            6   few
2011-03-01       94105    703.397213            6   few

In [11]:
zipcode = [item for item in set(houseprice.RegionName)]
zipcode

[94115, 94118, 94158, 94105, 94109, 94110, 94111]

In [12]:
zipcode.pop(2)

94158

In [13]:
plot_data = []

for i in xrange(len(zipcode)):   
    target = houseprice[houseprice.RegionName == zipcode[i]].dropna().sort_index()
    if set(target.group) == {'more'}:
        data1 = go.Scatter(
            x = target.index,
            y= target.Median_price,
            legendgroup = "more",
            connectgaps = True,
            name = str(zipcode[i]))
    else:
        data1 = go.Scatter(
            x = target.index,
            y= target.Median_price,
            legendgroup = "fewer",
            connectgaps = True,
            name = str(zipcode[i])+ " (fewer)",
            line = dict(dash = "dot"))        

    plot_data.append(data1)

    
layout= go.Layout(
    title= 'Housing Price From 2010 to 2017 In different Zipcode',
    hovermode= 'closest',
    yaxis= dict(
        title= 'Median Houseing Price',
        ticklen= 5,
        zeroline= False,
        gridwidth= 2,
        range = [200,1500]
    ),
    xaxis=dict(
        title= 'Year',
        ticklen= 5,
        gridwidth= 2)
)  
    
fig = go.Figure(data=plot_data, layout = layout)
iplot(fig)

<font color = "blue">
From the above plot, the dot line represent the zipcode with fewer school. In the begining, I expected that the more the school is, the higher the median housing price is. However, from the above plot, the price of two group do not have significant difference from 2010 to 2016. Therefore, we can conclude that the amount of school may not bring much influence on the house price in San Francisco. And the protentially reason might be that the median housing price in San Francisco are generally higher. The key factor for influencing housing price might be other factors. 

__2. Is the amount of food venders in weekday less than that during weekends?__

<font color = "blue">
In my opinion, I expected that the amount of food venders during weekend will be more than that in weekdays because people will go outside for recreation and tend to eat outside. In the economics aspect, when demand is higher. the supply will also higher. To confirm my inference, I did the following analysis. I count how many food vendors sell in each day of week and use bar plot to make it easier to find out when the food vendors are more.

In [14]:
vendorcount = pd.read_sql("SELECT DayOfWeek, count(distinct permit) as VendorCounts "
                          "FROM mobile_food_schedule GROUP By DayOfWeek ORDER By VendorCounts DESC"
                          , db)
vendorcount

DayOfWeek  VendorCounts
0        Fr           161
1        We           155
2        Th           153
3        Mo           148
4        Tu           148
5        Sa            96
6        Su            78

In [15]:
data = [go.Bar(
            x = vendorcount.DayOfWeek,
            y = vendorcount.VendorCounts,
            marker=dict(
            color=['rgba(204,204,204,1)','rgba(204,204,204,1)', 'rgba(204,204,204,1)','rgba(204,204,204,1)',
                  'rgba(204,204,204,1)','rgba(222,45,38,0.8)','rgba(222,45,38,0.8)']),
)]

layout = go.Layout(
    title = 'Number of Mobile Food Vendors Each Day',
    xaxis = dict(
        title= 'Day of Week',
        ticklen= 5,
        gridwidth= 2),
    yaxis = dict(
        title= 'Number of Vendors',
        ticklen= 5,
        gridwidth= 2),
    annotations=[
        dict(x=xi,y=yi,
             text=str(yi),
             xanchor='center',
             yanchor='bottom',
             showarrow = False,
        ) for xi, yi in zip(vendorcount.DayOfWeek, vendorcount.VendorCounts)]
)

fig = go.Figure(data=data, layout = layout)
iplot(fig)

<font color = "blue">
In the plot above, the red ones represent weekend and grey one represent weekday. It's totally different from my assumption. During weekends, the number of food vendors are nearly half or two-third of that in weekdays. According to this, I infer that that might because of the workers and officers. They have to work in weekdays and therefore mobile food vendors tend to sell in weekday to fulfill their requirement for food. Also, dring weekends, people might go to restaurants instead of having some hotdog from mobile food vendors.

__3. Which parks have most mobile food vendors nearby within 0.5 miles? Where are these parks?__

<font color = "blue">
Generally, the food vendors will be more in where are more crowded. Park is usually where people go for recreation and thus I expect the food vendors will be more near park. For this problem, I use the 4 tables including mobile_food_schedule, mobile_food_permits, mobile_food_locations, and park to find out which parks have more mobile food vendors within 0.5 miles. To calculate the distance between parks and vendors, I use geopy module to calculate the distance of two coordinates.

In [16]:
vendor_location = pd.read_sql("SELECT distinct l.locationid, Applicant , Latitude, Longitude "
                              "FROM mobile_food_permits AS p LEFT JOIN mobile_food_schedule as s "
                              "ON s.permit = p.permit "
                              "LEFT JOIN mobile_food_locations as l on s.locationid = l.locationid "
                              "WHERE Latitude <> 0 AND Longitude <> 0"
                              , db)
vendor_location.head(2)

locationid       Applicant   Latitude   Longitude
0      762178  F & C Catering  37.753109 -122.388170
1      762179  F & C Catering  37.754252 -122.389381

In [18]:
park = pd.read_sql("SELECT * FROM parks", db)
park = park.dropna()
park = park.reset_index(drop=True)

In [19]:
import geopy
from geopy.distance import vincenty

In [20]:
Allvendor_location = zip(vendor_location["Latitude"],vendor_location["Longitude"])
mile05 = []
for i in range(park.shape[0]):
    ploc = (park.ix[i,"Lat"],park.ix[i,"Lon"])
    dist = [vincenty(ploc, item).miles for item in Allvendor_location]
    mile05.append(len([j for j in xrange(len(dist)) if dist[j]<= 0.5]))

In [21]:
park_with_vendor = park.copy()
park_with_vendor["mile05"] = mile05
park_with_vendor = park_with_vendor.sort_values("mile05",ascending=False)
park_with_vendor.head(3)

Name                   Type  Acreage  ParkID  \
177                 ST MARY'S SQUARE  Civic Plaza or Square     1.11     136   
119                   MARITIME PLAZA  Civic Plaza or Square     2.01     142   
104  JUSTIN HERMAN/EMBARCADERO PLAZA  Civic Plaza or Square     4.33     138   

           Lat         Lon  mile05  
177  37.792056 -122.405117     108  
119  37.795605 -122.399239     107  
104  37.794880 -122.394766     103

<font color = "blue">
According to the above analysis, There are more food vendors near St. Mary Square and Maritime Plaza. We can use the following map to know their locations

In [23]:
data = go.Data([
        Scattermapbox(
            lat = [str(item) for item in list(vendor_location.Latitude)],
            lon = [str(item) for item in list(vendor_location.Longitude)],
            mode = 'markers',
            marker=go.Marker(dict(
                color =  "blue",
                size = 5)
            ),
            name = "vendors",
            hoverinfo = "none"
            ),
        Scattermapbox(
            lat = [str(item) for item in list(park_with_vendor.head(5).Lat)],
            lon = [str(item) for item in list(park_with_vendor.head(5).Lon)],
            mode = 'markers',
            text = [item for item in list(park_with_vendor.head(5).Name)],
            marker=go.Marker(dict(
                color =  "red",
                size = 15, 
                opacity = 0.7)
            ),
            hoverinfo='text',
            name = "park",

      )
    ])

layout = go.Layout(
    autosize=True,
    hovermode='closest',
    margin=go.Margin(
        l=100,
        r=100,
        b=50,
        t=50,
    ),
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=37.789056,
            lon=-122.408117
        ),
        pitch=0,
        zoom=12
    ),
    title = "Top 10 Park With Most Mobile Food Vendors Nearby Within 0.5 Mile"
)
fig = go.Figure(data=data, layout = layout)
iplot(fig)

<font color = "blue">
Based on the map, we can know the corresponding location of park and food vendors. It's clear that the food vendors appears more in the northeast and east of San Fransicso city. And the 5 park which have more food vendors nearby within 0.5 miles are also located in this district. We might infer that this district might be most bustling among all district in San Francisco.

__4. Which part of the city has more crime event in 2016?__

In [24]:
crime = pd.read_sql("SELECT DISTINCT * FROM crime "
                    "WHERE Datetime Between '2016-01-01 00:00:00' AND '2017-01-01 00:00:00'", db)

In [25]:
crime.shape

(149652, 10)

<font color = "blue">
In this problem, our goal is to find out which part of the city has more cirme incidents during 2016. However, there are 149652 cases in total and if we are plotting it on the map, the jupyter notebook will crash. Therefore, I implement samping method here. I randomly sampled 70000 case of them without replacement and use its location to find out which part of the city are there more cases.

In [26]:
import numpy as np
index = np.random.choice(xrange(crime.shape[0]),70000).tolist()

data = go.Data([{
        "hoverinfo" : "text",
        "lat" : [str(item) for item in list(crime.ix[index,:].Lat)],
        "lon" : [str(item) for item in list(crime.ix[index,:].Lon)],
        "marker":{
            "color": "red",
            "size" : 5,
        },
        "mode":"markers",
        "opacity":0.05,
        "name": "Crime",
        "type": "scattermapbox"}])


layout = go.Layout(
    autosize=True,
    hovermode='closest',
    margin=go.Margin(
        l=50,
        r=50,
        b=50,
        t=50,
    ),
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=37.7550704,
            lon=-122.43299268157651
        ),
        pitch=0,
        zoom=10.5,
        style = "light"
    ),
    title =  "Crime Map in San Francisco in 2016",
    showlegend = True,

)

fig = dict(data=data, layout=layout)
iplot(fig, filename = "Crime-in-2016")

<font color = "blue">
According to the map, although crime happened in every part of San Fransisco city but there are more cases happening in the northeast part. We can conclude that the northeasten San Fransisco is most dangerous. 

In specific, we can check which police district take responsibility of more cases.

In [27]:
crime_for_PdDist = pd.read_sql("SELECT PdDistrict, count(DISTINCT IncidntNum) as CrimeCount , "
                               "AVG(Lon) as Lon, AVG(Lat) as Lat "
                               "FROM crime WHERE PdDistrict <> 'NONE' "
                               "AND Datetime Between '2016-01-01 00:00:00' AND '2017-01-01 00:00:00' "
                               "GROUP BY PdDistrict ORDER BY CrimeCount DESC", db)
crime_for_PdDist

PdDistrict  CrimeCount         Lon        Lat
0    SOUTHERN       22139 -122.405265  37.779805
1    NORTHERN       15942 -122.426952  37.786639
2     MISSION       14445 -122.419507  37.760303
3     CENTRAL       14356 -122.409467  37.796903
4     BAYVIEW       10845 -122.393648  37.739959
5     TARAVAL        8738 -122.477883  37.738392
6   INGLESIDE        8634 -122.429490  37.727253
7    RICHMOND        7275 -122.473663  37.779384
8  TENDERLOIN        7008 -122.412539  37.783570
9        PARK        6827 -122.445653  37.770306

In [28]:
data = [go.Bar(
            x = crime_for_PdDist.PdDistrict,
            y = crime_for_PdDist.CrimeCount,
            name = "Crime Amount"
)]

layout = go.Layout(
    title = 'Number of Crime in 2016 For Each PD District',
    xaxis = dict(
        title= 'PdDistrict',
        ticklen= 10,
        gridwidth= 2),
    yaxis = dict(
        title= 'Number of Crime',
        ticklen= 10,
        gridwidth= 2),
    annotations=[
        dict(x=xi,y=yi,
             text=str(yi),
             xanchor='center',
             yanchor='bottom',
             showarrow = False,
        ) for xi, yi in zip(crime_for_PdDist.PdDistrict,crime_for_PdDist.CrimeCount)],
    showlegend = True
)

fig = go.Figure(data=data, layout = layout)
iplot(fig)

<font color = "blue">
According to the bar plot, Southern PdDistrict took responsibility of most crime events. After googling the location of southern pd District, I found out that southern pd District is the district that the point of the above map gathers.

__5. What kind of crime happen more often. At what time did these crime events happen?__ 

<font color = "blue">
There are lots of categories for crime. In this problem, I would like to discuss if different crime type happened in different time in a day. First of all, we can find out what kinf og crime happened more oftern through barplot.

In [37]:
type_ranking = pd.read_sql("SELECT Category, count(*) as no_case FROM crime "
                           "GROUP BY Category ORDER BY no_case DESC LIMIT 10",db)

In [38]:
data = [go.Bar(
            x = type_ranking.Category,
            y = type_ranking.no_case,
            name = "Case"
)]

layout = go.Layout(
    title = 'Number of Case for Each Crime Type',
    xaxis = dict(
        title= 'Category',
        ticklen= 10,
        gridwidth= 2),
    yaxis = dict(
        title= 'Number of Case',
        ticklen= 10,
        gridwidth= 2),
    annotations=[
        dict(x=xi,y=yi,
             text=str(yi),
             xanchor='center',
             yanchor='bottom',
             showarrow = False,
        ) for xi, yi in zip(type_ranking.Category,type_ranking.no_case)],
    showlegend = True
)

fig = go.Figure(data=data, layout = layout)
iplot(fig)

<font color = "blue">
The bar plot show the frequency of each crime type. It's clear that among top 10 crime types, LARCENY/THEFT happened more often. It's almost twice of the second place which is OTHER OFFENSES. In addition, the frequency of top 4 categories is clearly more than the other. 

In the next part, I will discuss when did this frequently happened crime take place. And for these part, we only focused on the top 5 crime types.

In [40]:
plot_data = []
for kind in type_ranking.Category.tolist()[:5]:
    data = pd.read_sql("SELECT strftime('%H',Datetime) as Hour, count(DISTINCT IncidntNum) as crime_per_hr FROM crime " 
                       "WHERE Category = '" +kind+ "' GROUP BY hour", db)
    plot_for_each_type = go.Scatter(
        x = data.Hour,
        y = data.crime_per_hr,
        legendgroup = "more",
        connectgaps = True,
        name = kind)
    plot_data.append(plot_for_each_type)

layout= go.Layout(
    title= 'Top 5 crime type in 24 hrs',
    hovermode= 'closest',
    yaxis= dict(
        title= 'Number of case',
        ticklen= 2,
        zeroline= False,
        gridwidth= 2,
    ),
    xaxis=dict(
        title= 'Hour',
        ticklen= 2,
        gridwidth= 2),
    showlegend= True
) 

fig = go.Figure(data=plot_data, layout = layout)
iplot(fig)

<font color = "blue">
The time series plot for the most 5 common crime categories showed that during midnight, there are less crime incident happening. At about 4am and 5pm, there are less crime incident reported. Larceny/Theft happened more often than others. And the frequency of it increase hours by hours after 5am and before 18pm. These 5 types of crime all have a peak during 12pm to 13pm. Something intersting is that Vandalism tends to happen more after evening. 